In [52]:
import os
import math
from docplex.mp.model import Model
from docplex.mp.relax_linear import LinearRelaxer

def fill_variables(file, n_customers, n_available_depots, coordinates_depots, coordinates_customers, v_capacity, capacities_depots,
        customers_demands, opening_costs_depots, opening_cost_route, zero_or_not):
    
    line = next(file)
    n_customers = int(line.strip())
    print("Número de customers: " + str(n_customers))
    line = next(file)
    n_available_depots = int(line.strip())
    print("Número de depots disponibles: " + str(n_available_depots))
    line = next(file)
    line = next(file)
            
    #coordenadas depots
    while(line.strip()):
        coordinates_depots.append(line.split())    
        line = next(file)
            
    #print("Coordenadas depots:")
    #print(coordinates_depots)
            
    line = next(file)
            
        #Coordenadas customers
    while(line.strip()):
        coordinates_customers.append(line.split())
                
        line = next(file)
            
    #print("Coordenadas customers:")
    #print(coordinates_customers)
            
    line = next(file)
            
    #Capacidad de vehículos
    v_capacity = int(line.strip())
    #print("Capacidad vehículos: " + v_capacity)
    line = next(file)
    line = next(file)
            
    #Capacidad de los depots
    while(line.strip()):
        capacities_depots.append(line.split())
                
        line = next(file)
            
    #print("Capacidades depots:")
    #print(capacities_depots)
            
    line = next(file)
            
    while(line.strip()):
        customers_demands.append(line.strip())
                
        line = next(file)
            
    #print("Demandas customers:")
    #print(customers_demands)
            
    line = next(file)
            
    while(line.strip()):
        opening_costs_depots.append(line.split())
                
        line = next(file)
            
    #print("Costos depots:")
    #print(opening_costs_depots)
            
    line = next(file)
            
            
    opening_cost_route = int(line.strip())
                
    line = next(file)
            
    #print("opening cost route:")
    #print(opening_cost_route)
            
    line = next(file)
    zero_or_not = int(line.strip())
            
    #print("zero o uno: " + zero_or_not)
    return [n_customers, n_available_depots, v_capacity, opening_cost_route, zero_or_not]
    
def distance_cost(a1, a2, b1, b2):
    a1 = int(a1)
    a2 = int(a2)
    b1 = int(b1)
    b2 = int(b2)
    x1 = a1-b1
    x2 = a2-b2
    x1 = pow(x1, 2)
    x2 = pow(x2, 2)
    return math.sqrt(x1 + x2)

In [64]:
file_path = "Inst1"
for filename in os.listdir(file_path):
    print("\nSiguiente archivo\n")
    f = os.path.join(file_path, filename)
    # checking if it is a file
    if os.path.isfile(f):
        
        #Contenedores de info inicializados en nada
        n_customers = 0
        n_available_depots = 0
        coordinates_depots = []
        coordinates_customers = []
        v_capacity = 0
        capacities_depots = []
        customers_demands = []
        opening_costs_depots = []
        opening_cost_route = 0
        zero_or_not = 1
        
        #Acá se toma la info de los archivos .dat
        with open(f, 'r') as file:
            lista_var = []
            lista_var = fill_variables(file, n_customers, n_available_depots, coordinates_depots, coordinates_customers, 
                                       v_capacity, capacities_depots, customers_demands, opening_costs_depots, 
                                       opening_cost_route, zero_or_not)
            n_customers = lista_var[0]
            n_available_depots = lista_var[1]
            v_capacity = lista_var[2]
            opening_cost_route = lista_var[3]
            zero_or_not = lista_var[4]
        
        #Empezar operaciones acá
        #distancias_d2d = []  VIAJE ENTRE 2 DEPOTS NO PERMITIDO
        distancias_d2c = []
        distancias_c2c = []
        distancias_c2d = []
        distancias = []
        
        #Acá se consiguen los c_ij (costos de caminos)
        for i in coordinates_depots:
            '''for j in coordinates_depots:
                if j==i:
                    continue
                distancias.append(distance_cost(i[0], i[1], j[0], j[1]))
                distancias_d2d.append(distance_cost(i[0], i[1], j[0], j[1]))'''
            for j in coordinates_customers:
                distancias.append(distance_cost(i[0], i[1], j[0], j[1]))
                distancias_d2c.append(distance_cost(i[0], i[1], j[0], j[1]))
        for i in coordinates_customers:
            for j in coordinates_depots:
                distancias.append(distance_cost(i[0], i[1], j[0], j[1]))
                distancias_c2d.append(distance_cost(i[0], i[1], j[0], j[1]))
                
        a=0
        for i in range(len(coordinates_customers)):
            for j in range(len(coordinates_customers)):
                b = coordinates_customers[i]
                c = coordinates_customers[j]
                if j==i:
                    continue
                distancias.append(distance_cost(b[0], b[1], c[0], c[1]))
                distancias_c2c.append(distance_cost(b[0], b[1], c[0], c[1]))
                
        print(a)
        #MODELO
        mdl = Model(name="MDRP")
        x = mdl.binary_var_list(len(distancias), name="x")
        mdl.print_information()
        
        #print(len(distancias))
        #C_ij * X_ij
        ab = [distancias[i]*x[i] for i in range(len(distancias))]
        mdl.minimize(mdl.sum(ab))

        #X_dj = yd
        for i in range(n_available_depots):
            offset = i*n_customers
            xdj = []
            for j in range(offset, offset+n_customers):
                xdj.append(x[j])
            mdl.add_constraint(sum(xdj) <= 1)
            mdl.add_constraint(sum(xdj) >= 0)
            
        #X_jd = yd
        for i in range(n_available_depots):
            xjd = []
            for j in range(n_customers):
                offset = j*n_available_depots + n_available_depots*n_customers
                #print(str(offset) + " vs " + str(len(distancias)) + " vs " + str(len(x)))
                xjd.append(x[offset])
            mdl.add_constraint(sum(xjd) <= 1)
            mdl.add_constraint(sum(xjd) >= 0)
        
        #F-MDRP para DL
        u = mdl.continuous_var_list(n_customers, name="u")
        for i in range(n_customers):
            offset_ij = 99*i + len(distancias_d2c) + len(distancias_c2d)
            for j in range(n_customers):
                if i==j:
                    continue
                offset_ji = 99*j + len(distancias_d2c) + len(distancias_c2d)
                #print(str(j + offset_ij) + " y " + str(i + offset_ji) + " contra " + str(len(x)))
                mdl.add_constraint(u[i] - u[j] + (n_customers-n_available_depots+1)*x[j + offset_ij] + (n_customers-n_available_depots-1)*x[i + offset_ji]  <= n_customers - n_available_depots)
                
        


Siguiente archivo

Número de customers: 100
Número de depots disponibles: 10
0
Model: MDRP
 - number of variables: 11900
   - binary=11900, integer=0, continuous=0
 - number of constraints: 0
   - linear=0
 - parameters: defaults
 - objective: none
 - problem type is: MILP
91x_2001+89x_2099+u_0-u_1 <= 90
91x_2002+89x_2198+u_0-u_2 <= 90
91x_2003+89x_2297+u_0-u_3 <= 90
91x_2004+89x_2396+u_0-u_4 <= 90
91x_2005+89x_2495+u_0-u_5 <= 90
91x_2006+89x_2594+u_0-u_6 <= 90
91x_2007+89x_2693+u_0-u_7 <= 90
91x_2008+89x_2792+u_0-u_8 <= 90
91x_2009+89x_2891+u_0-u_9 <= 90
91x_2010+89x_2990+u_0-u_10 <= 90
91x_2011+89x_3089+u_0-u_11 <= 90
91x_2012+89x_3188+u_0-u_12 <= 90
91x_2013+89x_3287+u_0-u_13 <= 90
91x_2014+89x_3386+u_0-u_14 <= 90
91x_2015+89x_3485+u_0-u_15 <= 90
91x_2016+89x_3584+u_0-u_16 <= 90
91x_2017+89x_3683+u_0-u_17 <= 90
91x_2018+89x_3782+u_0-u_18 <= 90
91x_2019+89x_3881+u_0-u_19 <= 90
91x_2020+89x_3980+u_0-u_20 <= 90
91x_2021+89x_4079+u_0-u_21 <= 90
91x_2022+89x_4178+u_0-u_22 <= 90
91x_2023

91x_2289+89x_11011+u_2-u_91 <= 90
91x_2290+89x_11110+u_2-u_92 <= 90
91x_2291+89x_11209+u_2-u_93 <= 90
91x_2292+89x_11308+u_2-u_94 <= 90
91x_2293+89x_11407+u_2-u_95 <= 90
91x_2294+89x_11506+u_2-u_96 <= 90
91x_2295+89x_11605+u_2-u_97 <= 90
91x_2296+89x_11704+u_2-u_98 <= 90
91x_2297+89x_11803+u_2-u_99 <= 90
89x_2003+91x_2297-u_0+u_3 <= 90
89x_2102+91x_2298-u_1+u_3 <= 90
89x_2201+91x_2299-u_2+u_3 <= 90
91x_2301+89x_2399+u_3-u_4 <= 90
91x_2302+89x_2498+u_3-u_5 <= 90
91x_2303+89x_2597+u_3-u_6 <= 90
91x_2304+89x_2696+u_3-u_7 <= 90
91x_2305+89x_2795+u_3-u_8 <= 90
91x_2306+89x_2894+u_3-u_9 <= 90
91x_2307+89x_2993+u_3-u_10 <= 90
91x_2308+89x_3092+u_3-u_11 <= 90
91x_2309+89x_3191+u_3-u_12 <= 90
91x_2310+89x_3290+u_3-u_13 <= 90
91x_2311+89x_3389+u_3-u_14 <= 90
91x_2312+89x_3488+u_3-u_15 <= 90
91x_2313+89x_3587+u_3-u_16 <= 90
91x_2314+89x_3686+u_3-u_17 <= 90
91x_2315+89x_3785+u_3-u_18 <= 90
91x_2316+89x_3884+u_3-u_19 <= 90
91x_2317+89x_3983+u_3-u_20 <= 90
91x_2318+89x_4082+u_3-u_21 <= 90
91x_2319+8

91x_2767+89x_9333+u_7-u_74 <= 90
91x_2768+89x_9432+u_7-u_75 <= 90
91x_2769+89x_9531+u_7-u_76 <= 90
91x_2770+89x_9630+u_7-u_77 <= 90
91x_2771+89x_9729+u_7-u_78 <= 90
91x_2772+89x_9828+u_7-u_79 <= 90
91x_2773+89x_9927+u_7-u_80 <= 90
91x_2774+89x_10026+u_7-u_81 <= 90
91x_2775+89x_10125+u_7-u_82 <= 90
91x_2776+89x_10224+u_7-u_83 <= 90
91x_2777+89x_10323+u_7-u_84 <= 90
91x_2778+89x_10422+u_7-u_85 <= 90
91x_2779+89x_10521+u_7-u_86 <= 90
91x_2780+89x_10620+u_7-u_87 <= 90
91x_2781+89x_10719+u_7-u_88 <= 90
91x_2782+89x_10818+u_7-u_89 <= 90
91x_2783+89x_10917+u_7-u_90 <= 90
91x_2784+89x_11016+u_7-u_91 <= 90
91x_2785+89x_11115+u_7-u_92 <= 90
91x_2786+89x_11214+u_7-u_93 <= 90
91x_2787+89x_11313+u_7-u_94 <= 90
91x_2788+89x_11412+u_7-u_95 <= 90
91x_2789+89x_11511+u_7-u_96 <= 90
91x_2790+89x_11610+u_7-u_97 <= 90
91x_2791+89x_11709+u_7-u_98 <= 90
91x_2792+89x_11808+u_7-u_99 <= 90
89x_2008+91x_2792-u_0+u_8 <= 90
89x_2107+91x_2793-u_1+u_8 <= 90
89x_2206+91x_2794-u_2+u_8 <= 90
89x_2305+91x_2795-u_3+u_8 <

91x_3425+89x_5875+u_14-u_39 <= 90
91x_3426+89x_5974+u_14-u_40 <= 90
91x_3427+89x_6073+u_14-u_41 <= 90
91x_3428+89x_6172+u_14-u_42 <= 90
91x_3429+89x_6271+u_14-u_43 <= 90
91x_3430+89x_6370+u_14-u_44 <= 90
91x_3431+89x_6469+u_14-u_45 <= 90
91x_3432+89x_6568+u_14-u_46 <= 90
91x_3433+89x_6667+u_14-u_47 <= 90
91x_3434+89x_6766+u_14-u_48 <= 90
91x_3435+89x_6865+u_14-u_49 <= 90
91x_3436+89x_6964+u_14-u_50 <= 90
91x_3437+89x_7063+u_14-u_51 <= 90
91x_3438+89x_7162+u_14-u_52 <= 90
91x_3439+89x_7261+u_14-u_53 <= 90
91x_3440+89x_7360+u_14-u_54 <= 90
91x_3441+89x_7459+u_14-u_55 <= 90
91x_3442+89x_7558+u_14-u_56 <= 90
91x_3443+89x_7657+u_14-u_57 <= 90
91x_3444+89x_7756+u_14-u_58 <= 90
91x_3445+89x_7855+u_14-u_59 <= 90
91x_3446+89x_7954+u_14-u_60 <= 90
91x_3447+89x_8053+u_14-u_61 <= 90
91x_3448+89x_8152+u_14-u_62 <= 90
91x_3449+89x_8251+u_14-u_63 <= 90
91x_3450+89x_8350+u_14-u_64 <= 90
91x_3451+89x_8449+u_14-u_65 <= 90
91x_3452+89x_8548+u_14-u_66 <= 90
91x_3453+89x_8647+u_14-u_67 <= 90
91x_3454+89x_8

89x_3502+91x_3698-u_15+u_17 <= 90
89x_3601+91x_3699-u_16+u_17 <= 90
91x_3701+89x_3799+u_17-u_18 <= 90
91x_3702+89x_3898+u_17-u_19 <= 90
91x_3703+89x_3997+u_17-u_20 <= 90
91x_3704+89x_4096+u_17-u_21 <= 90
91x_3705+89x_4195+u_17-u_22 <= 90
91x_3706+89x_4294+u_17-u_23 <= 90
91x_3707+89x_4393+u_17-u_24 <= 90
91x_3708+89x_4492+u_17-u_25 <= 90
91x_3709+89x_4591+u_17-u_26 <= 90
91x_3710+89x_4690+u_17-u_27 <= 90
91x_3711+89x_4789+u_17-u_28 <= 90
91x_3712+89x_4888+u_17-u_29 <= 90
91x_3713+89x_4987+u_17-u_30 <= 90
91x_3714+89x_5086+u_17-u_31 <= 90
91x_3715+89x_5185+u_17-u_32 <= 90
91x_3716+89x_5284+u_17-u_33 <= 90
91x_3717+89x_5383+u_17-u_34 <= 90
91x_3718+89x_5482+u_17-u_35 <= 90
91x_3719+89x_5581+u_17-u_36 <= 90
91x_3720+89x_5680+u_17-u_37 <= 90
91x_3721+89x_5779+u_17-u_38 <= 90
91x_3722+89x_5878+u_17-u_39 <= 90
91x_3723+89x_5977+u_17-u_40 <= 90
91x_3724+89x_6076+u_17-u_41 <= 90
91x_3725+89x_6175+u_17-u_42 <= 90
91x_3726+89x_6274+u_17-u_43 <= 90
91x_3727+89x_6373+u_17-u_44 <= 90
91x_3728+89x_6

...

94x_2174+96x_9426-u_11+u_85 <= 95
94x_2273+96x_9427-u_12+u_85 <= 95
94x_2372+96x_9428-u_13+u_85 <= 95
94x_2471+96x_9429-u_14+u_85 <= 95
94x_2570+96x_9430-u_15+u_85 <= 95
94x_2669+96x_9431-u_16+u_85 <= 95
94x_2768+96x_9432-u_17+u_85 <= 95
94x_2867+96x_9433-u_18+u_85 <= 95
94x_2966+96x_9434-u_19+u_85 <= 95
94x_3065+96x_9435-u_20+u_85 <= 95
94x_3164+96x_9436-u_21+u_85 <= 95
94x_3263+96x_9437-u_22+u_85 <= 95
94x_3362+96x_9438-u_23+u_85 <= 95
94x_3461+96x_9439-u_24+u_85 <= 95
94x_3560+96x_9440-u_25+u_85 <= 95
94x_3659+96x_9441-u_26+u_85 <= 95
94x_3758+96x_9442-u_27+u_85 <= 95
94x_3857+96x_9443-u_28+u_85 <= 95
94x_3956+96x_9444-u_29+u_85 <= 95
94x_4055+96x_9445-u_30+u_85 <= 95
94x_4154+96x_9446-u_31+u_85 <= 95
94x_4253+96x_9447-u_32+u_85 <= 95
94x_4352+96x_9448-u_33+u_85 <= 95
94x_4451+96x_9449-u_34+u_85 <= 95
94x_4550+96x_9450-u_35+u_85 <= 95
94x_4649+96x_9451-u_36+u_85 <= 95
94x_4748+96x_9452-u_37+u_85 <= 95
94x_4847+96x_9453-u_38+u_85 <= 95
94x_4946+96x_9454-u_39+u_85 <= 95
94x_5045+96x_9

94x_3070+96x_9930-u_20+u_90 <= 95
94x_3169+96x_9931-u_21+u_90 <= 95
94x_3268+96x_9932-u_22+u_90 <= 95
94x_3367+96x_9933-u_23+u_90 <= 95
94x_3466+96x_9934-u_24+u_90 <= 95
94x_3565+96x_9935-u_25+u_90 <= 95
94x_3664+96x_9936-u_26+u_90 <= 95
94x_3763+96x_9937-u_27+u_90 <= 95
94x_3862+96x_9938-u_28+u_90 <= 95
94x_3961+96x_9939-u_29+u_90 <= 95
94x_4060+96x_9940-u_30+u_90 <= 95
94x_4159+96x_9941-u_31+u_90 <= 95
94x_4258+96x_9942-u_32+u_90 <= 95
94x_4357+96x_9943-u_33+u_90 <= 95
94x_4456+96x_9944-u_34+u_90 <= 95
94x_4555+96x_9945-u_35+u_90 <= 95
94x_4654+96x_9946-u_36+u_90 <= 95
94x_4753+96x_9947-u_37+u_90 <= 95
94x_4852+96x_9948-u_38+u_90 <= 95
94x_4951+96x_9949-u_39+u_90 <= 95
94x_5050+96x_9950-u_40+u_90 <= 95
94x_5149+96x_9951-u_41+u_90 <= 95
94x_5248+96x_9952-u_42+u_90 <= 95
94x_5347+96x_9953-u_43+u_90 <= 95
94x_5446+96x_9954-u_44+u_90 <= 95
94x_5545+96x_9955-u_45+u_90 <= 95
94x_5644+96x_9956-u_46+u_90 <= 95
94x_5743+96x_9957-u_47+u_90 <= 95
94x_5842+96x_9958-u_48+u_90 <= 95
94x_5941+96x_9

94x_6045+96x_10455-u_50+u_95 <= 95
94x_6144+96x_10456-u_51+u_95 <= 95
94x_6243+96x_10457-u_52+u_95 <= 95
94x_6342+96x_10458-u_53+u_95 <= 95
94x_6441+96x_10459-u_54+u_95 <= 95
94x_6540+96x_10460-u_55+u_95 <= 95
94x_6639+96x_10461-u_56+u_95 <= 95
94x_6738+96x_10462-u_57+u_95 <= 95
94x_6837+96x_10463-u_58+u_95 <= 95
94x_6936+96x_10464-u_59+u_95 <= 95
94x_7035+96x_10465-u_60+u_95 <= 95
94x_7134+96x_10466-u_61+u_95 <= 95
94x_7233+96x_10467-u_62+u_95 <= 95
94x_7332+96x_10468-u_63+u_95 <= 95
94x_7431+96x_10469-u_64+u_95 <= 95
94x_7530+96x_10470-u_65+u_95 <= 95
94x_7629+96x_10471-u_66+u_95 <= 95
94x_7728+96x_10472-u_67+u_95 <= 95
94x_7827+96x_10473-u_68+u_95 <= 95
94x_7926+96x_10474-u_69+u_95 <= 95
94x_8025+96x_10475-u_70+u_95 <= 95
94x_8124+96x_10476-u_71+u_95 <= 95
94x_8223+96x_10477-u_72+u_95 <= 95
94x_8322+96x_10478-u_73+u_95 <= 95
94x_8421+96x_10479-u_74+u_95 <= 95
94x_8520+96x_10480-u_75+u_95 <= 95
94x_8619+96x_10481-u_76+u_95 <= 95
94x_8718+96x_10482-u_77+u_95 <= 95
94x_8817+96x_10483-u

Model: MDRP
 - number of variables: 580
   - binary=580, integer=0, continuous=0
 - number of constraints: 0
   - linear=0
 - parameters: defaults
 - objective: none
 - problem type is: MILP
16x_201+14x_299+u_0-u_1 <= 15
16x_202+14x_398+u_0-u_2 <= 15
16x_203+14x_497+u_0-u_3 <= 15


IndexError: list index out of range